#  Tone Classification Task

## Data Preparation

In [76]:
require 'loader'
require 'nn'
MAX_LEN = 256
max_len = 64
-- Loader:new(obj, max_len)
ldr = Loader:new(nil, MAX_LEN)

In [77]:
function moving_avg(vec, window)
    local len = (#vec)[1]
    local new_vec = torch.Tensor(len):fill(0.0)
    for i = 1, (len - window - 1) do
        local sum = vec[{{i, i + window - 1}}]:sum() / window
        new_vec[i+1] = sum
    end
    return new_vec
end

In [78]:
-- kick too large or too small values
function kick(vec, topsmall, toplarge)
    -- kick the smalls
    for i = 1, topsmall do
        vec:csub(vec:min())
        new_vec = vec[vec:gt(0.0)]:clone()
        vec = new_vec
    end
    for i = 1, toplarge do
        _, inds = torch.max(vec, 1)
--         print(inds)
--         for j = 1, (#inds)[1] do
--             vec[inds[j]] = 0.0
--         end
        vec[inds[1]] = 0.0
        vec[inds[-1]] = 0.0
        new_vec = vec[vec:gt(0.0)]:clone()
        vec = new_vec
    end
    return new_vec
end

-- local i = 0
-- local tester = torch.Tensor(10):apply(function() i = i + 1 return i end)
-- print(tester)
-- print(kick(tester, 1, 0))

In [79]:
local matrix = require "matrix"
local fit = {}
local function getresults( mtx )
    assert( #mtx+1 == #mtx[1], "Cannot calculate Results" )
    mtx:dogauss()
    -- tresults
    local cols = #mtx[1]
    local tres = {}
    for i = 1,#mtx do
        tres[i] = mtx[i][cols]
    end
    return unpack( tres )
end

function fit.parabola( x_values,y_values )
    -- x_values = { x1,x2,x3,...,xn }
    -- y_values = { y1,y2,y3,...,yn }

    -- values for A matrix
    local a_vals = {}
    -- values for Y vector
    local y_vals = {}

    for i,v in ipairs( x_values ) do
        a_vals[i] = { 1, v, v*v }
        y_vals[i] = { y_values[i] }
    end

    -- create both Matrixes
    local A = matrix:new( a_vals )
    local Y = matrix:new( y_vals )

    local ATA = matrix.mul( matrix.transpose(A), A )
    local ATY = matrix.mul( matrix.transpose(A), Y )

    local ATAATY = matrix.concath(ATA,ATY)

    return getresults( ATAATY )
end

function fit_quad(vec, targetLen)
    local len = (#vec)[1]
    local xs = {}
    local ys = {}
    local a, b, c
    for i = 1, len do
        table.insert(xs, i)
        table.insert(ys, vec[i])
    end
    a, b, c = fit.parabola(xs, ys)
    local res = torch.Tensor(targetLen)
    for i = 1, targetLen do
        local ii = (i - 1) / (targetLen - 1) * (len - 1) + 1
        res[i] = a + b * ii + c * ii * ii
    end
    return res, {a, b, c}
end

function fit_tail(vec, targetLen, portion)
    local len = (#vec)[1]
    local start = math.modf(len * portion)
    local xs = {}
    local ys = {}
    local a, b, c
    for i = 1, len - start do
        table.insert(xs, i)
        table.insert(ys, vec[i + start])
    end
    a, b, c = fit.parabola(xs, ys)
    local res = torch.Tensor(targetLen)
    for i = 1, targetLen do
        local ii = (i - 1) / (targetLen - 1) * (len - start - 1) + 1
        res[i] = a + b * ii + c * ii * ii
    end
    return res, {a, b, c}
end

In [80]:
function make_linear_spine(vec, targetLen)
    local len = (#vec)[1]
    local ys = {}
    
    for i = 1, len do
        table.insert(ys, vec[i])
    end
    
    local res
    local coef
    res, coef = torch.Tensor(targetLen)
    
    local i = 1
    for ind = 1, targetLen do
        local x = (ind - 1) * (len - 1) / (targetLen - 1) + 1
        if  x > i then
            i = i + 1
        end
        if x == i then 
            res[ind] = ys[i]
        else
            res[ind] = (ys[i] - ys[i - 1]) * (x - i + 1) + ys[i - 1]
        end
    end
    return res, coef
end

# Dataset!

In [81]:
function make_dataset(name, mode)
    local ldr = Loader:new(nil, 256)
    local collection = {data = ldr.data[name]:float(), label = ldr.label[name]}
    function collection:size() 
        return self.data:size(1) 
    end
    
    -- Mel Frequency
    for j = 1, collection:size() do
        collection.data[{j, {}, 1}]:div(700):log1p():mul(5975.208)
    end
    
    -- local standardization
    for i = 1, 2 do
        for j = 1, collection:size() do
            local std = collection.data[{j, {}, i}]:std()
            collection.data[{j, {}, i}]:div(std)
        end
    end

    -- global standardization
    for i = 1, 2 do
        local std = collection.data[{{}, {}, i}]:std()
        collection.data[{{}, {}, i}]:div(std)
    end

    local resized_collection = {
        data = torch.Tensor(collection:size(), max_len,2):float(),
        label = collection.label
    }
    -- filter noice and shif to the beginning
    local coef = {}
    for i = 1, collection:size() do
        for j = 1, 256 do
            if (collection.data[{i, j, 2}] < 1.0) then
                collection.data[{i, j, 1}] = 0.0
                collection.data[{i, j, 2}] = 0.0
            end
        end
        local shifted_F0 = torch.Tensor(max_len):fill(0.0)
        local shifted_Engy = torch.Tensor(max_len):fill(0.0)
        local data = collection.data[{i, {}, {}}]
        local tmpF0 = data[{{}, 1}][data[{{}, 1}]:gt(0.0)]:clone()
        local tmpEngy = data[{{}, 2}][data[{{}, 2}]:gt(0.0)]:clone()
        
        peek = tmpF0
--         smooth (refer to a paper)
--         tmpF0 = tmpF0:index(1 ,torch.linspace((#tmpF0)[1],1,(#tmpF0)[1]):long())
        local tmpF0_prime = tmpF0:clone()
        local c_1 = 0.3
        local c_2 = 0.5
        -- half or double
        for j = 2, (#tmpF0)[1] do
            if math.abs(tmpF0[j] / 2 - tmpF0[j - 1]) < c_1 then 
                tmpF0[j] = tmpF0[j] / 2
            elseif math.abs(2 * tmpF0[j] - tmpF0[j - 1]) < c_1 then
                tmpF0[j] = tmpF0[j] * 2
            end
        end
        -- random error
        for j = 3, (#tmpF0)[1] - 1 do
            if math.abs(tmpF0[j] - tmpF0_prime[j - 1]) > c_1 and math.abs(tmpF0[j + 1] - tmpF0_prime[j - 1]) > c_2 then
                tmpF0_prime[j] = 2 * tmpF0_prime[j - 1] - tmpF0_prime[j - 2]
            elseif math.abs(tmpF0[j] - tmpF0_prime[j - 1]) > c_1 and math.abs(tmpF0[j + 1] - tmpF0_prime[j - 1]) <= c_2 then
                tmpF0_prime[j] = 0.5 * (tmpF0_prime[j - 1] + tmpF0[j + 1])
            else 
                tmpF0_prime[j] = tmpF0[j] 
            end
        end
        -- backward check
        for j = (#tmpF0)[1] - 2, 2, -1 do
            if math.abs(tmpF0_prime[j] - tmpF0_prime[j + 1]) > c_1 and math.abs(tmpF0_prime[j - 1] - tmpF0_prime[j + 1]) > c_2 then
                tmpF0[j] = 2 * tmpF0_prime[j + 1] - tmpF0_prime[j + 2]
            elseif math.abs(tmpF0_prime[j] - tmpF0_prime[j - 1]) > c_1 and math.abs(tmpF0_prime[j + 1] - tmpF0_prime[j - 1]) <= c_2 then
                tmpF0[j] = 0.5 * (tmpF0_prime[j + 1] + tmpF0_prime[j - 1])
            else 
                tmpF0[j] = tmpF0_prime[j]
            end
            if math.abs(tmpF0_prime[j] - tmpF0[j]) < c_1 then
                for k = 1, j - 1 do
                    tmpF0[k] = tmpF0_prime[k]
                end
                break
            end
        end
--         tmpF0:index(1 ,torch.linspace((#tmpF0)[1],1,(#tmpF0)[1]):long())
        
--         tmpF0 = kick(tmpF0, 1, 0)
--         tmpEngy = kick(tmpEngy, 1, 0)
        
--         local cut_len = (#tmpF0)[1] * 0.25
--         tmpF0 = tmpF0[{{cut_len, -1}}]

        -- smooth
        tmpF0 = moving_avg(tmpF0, 5)
        tmpF0 = tmpF0[tmpF0:gt(0.0)]:clone()
        tmpEngy = moving_avg(tmpEngy, 5)
        tmpEngy = tmpEngy[tmpEngy:gt(0.0)]:clone()

        if mode == 'shift' then
            shifted_F0[{{2, (#tmpF0)[1] + 1}}] = tmpF0
            shifted_Engy[{{2, (#tmpEngy)[1] + 1}}] = tmpEngy
            resized_collection.data[{i, {}, 1}] = shifted_F0
            resized_collection.data[{i, {}, 2}] = shifted_Engy
        elseif mode == 'quad' then
            resized_collection.data[{i, {}, 1}], coef[i] = fit_quad(tmpF0, max_len)
            resized_collection.data[{i, {}, 2}] = fit_quad(tmpEngy, max_len)
        elseif mode == 'linear' then
            resized_collection.data[{i, {}, 1}] = make_linear_spine(tmpF0, max_len)
            resized_collection.data[{i, {}, 2}] = make_linear_spine(tmpEngy, max_len)
        end
    end
--     for i = 1, 2 do
--         for j = 1, dataset:size() do
--             local std = resized_collection.data[{j, {}, i}]:std()
--             resized_collection.data[{j, {}, i}]:div(std)
--         end
--     end
    for i = 1, 2 do
        for j = 1, collection:size() do
            local mean = resized_collection.data[{j, {}, i}]:mean()
            resized_collection.data[{j, {}, i}]:csub(mean)
--             local mean = resized_collection.data[{j, {}, i}][-1]
--             resized_collection.data[{j, {}, i}]:csub(mean)
--             local std = resized_collection.data[{{}, {}, i}]:std()
--             resized_collection.data[{{}, {}, i}]:div(std)
        end
    end
    for i = 1, 2 do
        local std = resized_collection.data[{{}, {}, i}]:std()
        resized_collection.data[{{}, {}, i}]:div(std)
    end
    
    resized_collection.data[{{}, {}, 2}]:fill(0.0)
    for i = 1, collection:size() do
        resized_collection[i] = {resized_collection.data[i], resized_collection.label[i]}
    end
    print("dataset "..name.." has been constructed!")
    return resized_collection, coef
end

In [106]:
trainset, tarincoef = make_dataset('train', 'linear')
testset, testcoef = make_dataset('test', 'linear')
newtestset, newtestcoef = make_dataset('test_new', 'linear')

dataset train has been constructed!	


dataset test has been constructed!	


dataset test_new has been constructed!	


In [72]:
Plot = require 'itorch.Plot'
local x1 = torch.range(1,max_len)
local sampleN = 400
-- local y2 = newtestset.data[{sampleN,{},2}]
-- local x1 = torch.range(1,18)
-- local y1 = peek
plot = Plot():title('Feature Observation of Tones')
for i = 1, sampleN do
    local y1 = trainset.data[{i,{},1}]
    if i <= 100 then plot:line(x1, y1,'red','f0') 
    elseif i <= 200 then plot:line(x1, y1,'blue','f0')
    elseif i <= 300 then plot:line(x1, y1,'green','f0')
    else plot:line(x1, y1,'black','f0') end
end
plot:redraw()

In [73]:
Plot = require 'itorch.Plot'
local sampleN = 400
-- local y2 = newtestset.data[{sampleN,{},2}]
-- local x1 = torch.range(1,18)
-- local y1 = peek
plot = Plot():title('Feature Observation of Tones')
for i = 1, sampleN do
    local x1 = {tarincoef[i][1]}
    local y1 = {tarincoef[i][3]}
    if i <= 100 then plot:circle(x1, y1,'red','f0') 
    elseif i <= 200 then plot:circle(x1, y1,'blue','f0')
    elseif i <= 300 then plot:circle(x1, y1,'green','f0')
    else plot:circle(x1, y1,'black','f0') end
end
plot:redraw()

In [74]:
Plot = require 'itorch.Plot'
local x1 = torch.range(1,max_len)
local sampleN = 226
-- local y2 = newtestset.data[{sampleN,{},2}]
-- local x1 = torch.range(1,18)
-- local y1 = peek
plot = Plot():title('Feature Observation of Tones')
for i = 1, sampleN do
    local y1 = newtestset.data[{i,{},1}]
    if i <= 54 then plot:line(x1, y1,'red','f0')
--     if i <= 54 then 
    elseif i <= 114 then plot:line(x1, y1,'blue','f0')
    elseif i <= 174 then plot:line(x1, y1,'green','f0')
    else plot:line(x1, y1,'black','f0') end
end
plot:redraw()

In [75]:
Plot = require 'itorch.Plot'
local sampleN = 226
-- local y2 = newtestset.data[{sampleN,{},2}]
-- local x1 = torch.range(1,18)
-- local y1 = peek
plot = Plot():title('Feature Observation of Tones')
for i = 1, sampleN do
    local x1 = {newtestcoef[i][2]}
    local y1 = {newtestcoef[i][3]}
    if i <= 54 then plot:circle(x1, y1,'red','f0') 
    elseif i <= 114 then plot:circle(x1, y1,'blue','f0')
    elseif i <= 174 then plot:circle(x1, y1,'green','f0')
    else plot:circle(x1, y1,'black','f0') end
end
plot:redraw()

In [102]:
peek

 2.7582
 2.9331
 3.0379
 3.1390
 3.2025
 3.2660
 3.3295
 3.3930
 3.4565
 3.5200
 3.3657
 3.2113
 3.1614
 3.0501
 2.9771
 2.8889
 2.8337
 2.8231
 2.8037
 2.7307
 2.6745
 2.6150
 2.5463
 2.4992
 2.3712
 2.3180
 2.2314
 2.1570
 2.0885
 2.0196
 1.9625
 1.9148
 1.8748
 1.8422
 1.7960
 1.7475
[torch.FloatTensor of size 36]



# Model

In [120]:
require 'dp'
local inp = 2;  -- dimensionality of one sequence element 
local outp = 4; -- number of derived features for one sequence element
local conv_kw = 4;   -- number of sequence element kernel operates on per step
local conv_dw = 4;   -- step dw and go on to the next sequence element

local pool_kw = 4;   -- number of sequence element pooled on per step
local pool_dw = 4;   -- step dw and go on to the next sequence element

local nOutputFrame = (max_len - conv_kw) / conv_dw + 1
local nOutputFrame = (nOutputFrame - pool_kw) / pool_dw + 1

net = nn.Sequential()
peek = nn.TemporalConvolution(inp, outp, conv_kw, conv_dw)
net:add(peek)
net:add(nn.ReLU())
net:add(nn.TemporalMaxPooling(pool_kw, pool_dw))
net:add(nn.View(outp*nOutputFrame))
net:add(nn.Linear(outp*nOutputFrame, 128))
-- net:add(nn.BatchNormalization(64))
net:add(nn.ReLU())
net:add(nn.Linear(128, 4))
net:add(nn.LogSoftMax())

In [121]:
print (net:__tostring())

nn.Sequential {
  [input -> (1) -> (2) -> (3) -> (4) -> (5) -> (6) -> (7) -> (8) -> output]
  (1): nn.TemporalConvolution
  (2): nn.ReLU
  (3): nn.TemporalMaxPooling
  (4): nn.View(16)
  (5): nn.Linear(16 -> 128)
  (6): nn.ReLU
  (7): nn.Linear(128 -> 4)
  (8): nn.LogSoftMax
}	


In [122]:
criterion = nn.ClassNLLCriterion();  
trainer = nn.StochasticGradient(net, criterion)  
trainer.learningRate = 0.001
trainer.maxIteration = 200
trainer.verbose = False

In [123]:
function cal_acc(dataset)
    local acc = 0.0
    for i = 1, dataset:size() do
        _, output = torch.max(net:forward(dataset[i][1]), 1)
        if output[1] == dataset[i][2] then
            acc = acc + 1.0
        end
    end
    acc = acc / dataset:size()
    return acc
end

In [124]:
recorder = {loss = {}, trainacc = {}, valacc = {}, testacc = {}}
trainer.hookIteration = function(obj, iteration, currentError) 
    local trainacc = cal_acc(trainset)
    local valacc = cal_acc(testset)
    local testacc = cal_acc(newtestset)
    table.insert(recorder.loss, currentError)
    table.insert(recorder.trainacc, trainacc)
    table.insert(recorder.valacc, valacc)
    table.insert(recorder.testacc, testacc)
    if (iteration % 10 == 0) then 
        print('Iteration '..iteration..': loss('..currentError..') train_acc('
            ..trainacc..') test_acc('..valacc..') new_test_acc('..testacc..').')
    end
end

In [125]:
trainer:train(trainset)

...RZ/torch/install/share/lua/5.1/nn/StochasticGradient.lua:19: attempt to call method 'size' (a nil value)
stack traceback:
	...RZ/torch/install/share/lua/5.1/nn/StochasticGradient.lua:19: in function 'f'
	[string "local f = function() return trainer:train(tra..."]:1: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

In [16]:
local x = torch.range(1, #recorder.loss)
plt = Plot():line(x, recorder.loss,'red','loss'):legend(true):title('Train Loss'):draw()
plt = Plot():line(x, recorder.trainacc,'blue','train_acc'):legend(true):title('Accuracy'):draw()
plt:line(x, recorder.valacc,'green','val_acc'):redraw()

bad argument #2 to '?' (upper bound and larger bound incoherent with step sign at /Users/YRZ/torch/pkg/torch/lib/TH/generic/THTensorMath.c:1457)
stack traceback:
	[C]: at 0x0b4ee170
	[C]: in function 'range'
	[string "local x = torch.range(1, #recorder.loss)..."]:1: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

In [17]:
print ('accuracy on train set '..cal_acc(trainset))
print ('accuracy on test set '..cal_acc(testset))
print ('accuracy on new test set '..cal_acc(newtestset))

[string "function cal_acc(dataset)..."]:3: attempt to call method 'size' (a nil value)
stack traceback:
	[string "function cal_acc(dataset)..."]:3: in function 'cal_acc'
	[string "print ('accuracy on train set '..cal_acc(trai..."]:1: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

## To see why

In [18]:
mislabeled = {}
local output
for i = 1, newtestset:size() do
    _, output = torch.max(net:forward(newtestset[i][1]), 1)
    if output[1] ~= newtestset[i][2] then
        table.insert(mislabeled, { data_id = i, pred = output[1], gt = newtestset[i][2]})
    end
end

[string "mislabeled = {}..."]:3: attempt to call method 'size' (a nil value)
stack traceback:
	[string "mislabeled = {}..."]:3: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

In [19]:
print(#mislabeled)

0	


In [20]:
print(mislabeled)

In [21]:
print(net:forward(newtestset[4][1]))
-- print(peek:forward(newtestset[4][1]))
print(peek.weight)
-- local x1 = torch.range(1, MAX_LEN - 1)
-- local sampleN = 7
-- local y1 = newtestset.data[{sampleN,{},1}]
-- local y2 = peek
-- plot = Plot():line(x1, y1,'red','f0'):legend(true):title('Feature Observation of a Tone '..newtestset.label[sampleN]):draw()
-- plot:line(x1, y2,'blue','engy'):redraw()

/Users/YRZ/torch/install/share/lua/5.1/nn/Container.lua:67: 
In 1 module of nn.Sequential:
/Users/YRZ/torch/install/share/lua/5.1/nn/THNN.lua:110: bad argument #3 to 'v' (cannot convert 'struct THDoubleTensor *' to 'struct THFloatTensor *')
stack traceback:
	[C]: in function 'v'
	/Users/YRZ/torch/install/share/lua/5.1/nn/THNN.lua:110: in function 'TemporalConvolution_updateOutput'
	...Z/torch/install/share/lua/5.1/nn/TemporalConvolution.lua:41: in function <...Z/torch/install/share/lua/5.1/nn/TemporalConvolution.lua:40>
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/nn/Container.lua:63: in function 'rethrowErrors'
	/Users/YRZ/torch/install/share/lua/5.1/nn/Sequential.lua:44: in function 'forward'
	[string "print(net:forward(newtestset[4][1]))..."]:1: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq

## Try Rules!

In [22]:
function cal_acc_rule(dataset)
    local acc = 0.0
    for i = 1, dataset:size() do
        output = simple_rule(dataset[i][1])
        if output == dataset[i][2] then
            acc = acc + 1.0
        end
    end
    acc = acc / dataset:size()
    return acc
end

In [23]:
function simple_rule(example)
    -- only take f0
    local f0 = example[{{}, 1}]
    local max = f0:max()
    if max < 0.3 then return 1 end
    local totcnt = 0
    local cnt = 0
    for i = 1, (#f0)[1] - 1 do
        if f0[i + 1] ~= 0 then totcnt = totcnt + 1 end
        if f0[i + 1] - f0[i] < 0 then cnt = cnt + 1 end
    end
    if cnt > 0.8 * totcnt then return 4
    elseif cnt < 0.2 * totcnt then return 2
    else return 3 end
end

In [24]:
print ('accuracy on train set '..cal_acc_rule(trainset))
print ('accuracy on test set '..cal_acc_rule(testset))
print ('accuracy on new test set '..cal_acc_rule(newtestset))

[string "function cal_acc_rule(dataset)..."]:3: attempt to call method 'size' (a nil value)
stack traceback:
	[string "function cal_acc_rule(dataset)..."]:3: in function 'cal_acc_rule'
	[string "print ('accuracy on train set '..cal_acc_rule..."]:1: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

In [25]:
mislabeled_rule = {}
local output
for i = 1, newtestset:size() do
    local output = simple_rule(newtestset[i][1])
    if output ~= newtestset[i][2] then
        table.insert(mislabeled_rule, { data_id = i, pred = output, gt = newtestset[i][2]})
    end
end

[string "mislabeled_rule = {}..."]:3: attempt to call method 'size' (a nil value)
stack traceback:
	[string "mislabeled_rule = {}..."]:3: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

In [26]:
print(#mislabeled_rule)

In [27]:
print(mislabeled_rule)

In [28]:
local i = 1.5
local x = torch.Tensor{i, i * i}:reshape(1,2)
print(x)

{
}


 1.5000  2.2500
[torch.DoubleTensor of size 1x2]



In [29]:
function make_linear_spine(vec, targetLen)
    local len = (#vec)[1]
    local ys = {}
    
    for i = 1, len do
        table.insert(ys, vec[i])
    end
    
    local res = torch.Tensor(targetLen)
    
    local i = 1
    for ind = 1, targetLen do
        local x = (ind - 1) * (len - 1) / (targetLen - 1) + 1
        if  x > i then
            i = i + 1
        end
        if x == i then 
            res[ind] = ys[i]
        else
            res[ind] = (ys[i] - ys[i - 1]) * (x - i + 1) + ys[i - 1]
        end
    end
    return res
end

In [30]:
-- print(peek)
print(make_linear_spine(peek, 64))
-- fit_quad(peek)

[string "function make_linear_spine(vec, targetLen)..."]:2: nn.TemporalConvolution has no length operator
stack traceback:
	[C]: in function '__len'
	[string "function make_linear_spine(vec, targetLen)..."]:2: in function 'make_linear_spine'
	[string "-- print(peek)..."]:2: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

In [107]:
function toTable(vec)
    local tmp = {}
    for i = 1, (#vec)[1] do
       tmp[i] = vec[i] 
    end
    return tmp
end
local cjosn = require 'cjson'
function makeJson(indata)
    local k = (#indata.data)[1]
    local aryDatas = {}
    for i = 1, k do
        aryDatas[i] = {}
        aryDatas[i]["label"] = indata.label[i]
        aryDatas[i]["input"] = toTable(indata.data[{i, {}, 1}])
    end
    return aryDatas
end
local jsonTable = {};
jsonTable['train'] = makeJson(trainset)
jsonTable['test'] = makeJson(testset)
jsonTable['test_new'] = makeJson(newtestset)
local jsonStr = cjson.encode(jsonTable)
file = io.open("data_linear.json", "w+")
file:write(jsonStr)